In [1]:
# Standard-Importe
import io
import csv
from zipfile import ZipFile 

# nd array
import numpy as np

# Bildverarbeitung
#from skimage.transform import rescale, resize
from PIL import Image, ImageOps
from skimage.color import rgb2gray, rgb2hsv

# Anzeigen
import matplotlib.pyplot as plt

# Interaktionsmöglichkeiten
from ipywidgets import interact, IntSlider

#Keras lernendes System
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.python.keras.layers import Input, Dense
from keras.models import Sequential
from keras.layers import Convolution2D
from keras.layers import MaxPooling2D
from keras.layers import Flatten
from keras.utils import np_utils
from keras.datasets import mnist
print(tf.__version__)


#Zip importierer
def read_traffic_signs_from_zip(Verkehrszeichen):
    '''Reads traffic sign data for German Traffic Sign Recognition Benchmark.

    Arguments: path to the traffic sign data zip file, for example 'Verkehrszeichen.zip'
    Returns:   images_original, images_gray, labels'''
    
    images_original = [] # Original-Bilder unbearbeitet
    images_gray     = [] # Grauwertbilder, ausgeschitten und 50 x 50 groß
    labels          = [] # Klassen-Labels
    
    # Zip-file öffnen
    with ZipFile(Verkehrszeichen, 'r') as zip_file:
        
        # loop over all 43 classes
        for c in range(0, 43):
            # Verzeichnis für Klasse in der Zip-Datei
            prefix = format(c, '05d') + '/' 
            
            # Annotation Datei
            annotation_file_name = prefix + 'GT-' + format(c, '05d') + '.csv'
            
            with io.TextIOWrapper(zip_file.open(annotation_file_name), encoding="utf-8") as annotation_file:
                
                # CSV Datei lesen
                data_reader = csv.reader(annotation_file, delimiter=';')
                next(data_reader) # skip header

                # loop over all images in current annotations file
                for row in data_reader:
                    # Dateiname aus CSV Datei lesen
                    # In der ersten Spalte (Index 0) steht der Dateiname
                    image_file_name = prefix + row[0]
                    
                    # Bilddatei öffnen
                    with zip_file.open(image_file_name) as img_file:                        
                        # ROI aus CSV-Datei lesen
                        x1 = int(row[3])
                        y1 = int(row[4])
                        x2 = int(row[5])
                        y2 = int(row[6])
                        
                        # Image Objekt, viele Datei-Typen über PIL verfügbar
                        # Datei laden
                        img_ = Image.open(img_file)   
                        
                        # ausschneiden
                        img_crop = img_.crop((x1, y1, x2, y2))
                        
                        # Größe ändern
                        img = img_crop.resize((50, 50), resample=Image.LANCZOS)
                        
                        # np arrays, Farbtransformation
                        img_orig = np.array(img)               # uint8
                        img_gray = rgb2gray(img_orig)
                        
                        # Datentyp ändern
                        img_gray = img_gray.astype(np.float32) # float64 -> float32
                        
                         # in Listen speichern
                        images_original.append(img_orig)
                        images_gray.append(img_gray)
                     
                        # Klassenlabel 0...42
                        labels.append(int(row[7])) # In der 8. Spalte steht der Klassen-Label.
                        
        
    return images_original, images_gray, labels

images_original, images_gray, labels = read_traffic_signs_from_zip('Verkehrszeichen.zip')


images_original = np.asarray(images_original)
print(images_original.shape, images_original.dtype)
# Datensatz aufteilen
np.random.seed(42)

# Anzahl der Daten
percent_train = 0.8 # 80% für Trainingszwecke

#Traingsdaten von Testdata trennen
labels = np.asarray(labels)
nof_data = labels.shape[0]
nof_train = int(nof_data*percent_train)

# gesamte Datenmenge
dataset = images_original.astype(np.float64)

# Skalieren auf den Bereich 0.01 - 1.0
dataset = (dataset / 255.0 * 0.98) + 0.01
print('min = {0}, max = {1}'.format(dataset.min(), dataset.max()))

# Biasvektor
dataset[:,-1] = 1.0

# gesamte Klassenlabels (überwachtes Lernen)
labelset = labels.astype(np.int32)
print('dataset: ', dataset.shape, dataset.dtype)
print('labelset:', labelset.shape)

# -- Daten aufteilen --

# Zufällige Indizes der Trainingsmenge
all_idx   = np.arange(nof_data)
train_idx = np.random.choice(nof_data, nof_train, replace=False)
test_idx  = np.delete(all_idx, train_idx)

# Trainingsvektoren (Zeilen) auswählen
x_train = dataset[train_idx]
c_train = labelset[train_idx]

# Testvektoren (Zeilen) auswählen
x_test  = dataset[test_idx]
c_test  = labelset[test_idx]

#############################################################
XTrain = x_train
YTrain = np.ones((c_train.shape[0],43)) * 0.01
for i in range(YTrain.shape[0]):
    number = c_train[i]  # Klasse
    YTrain[i, number] = 0.99
print(YTrain.shape, YTrain.dtype)
    
XTest  = x_test
YTest = np.ones((c_test.shape[0],43)) * 0.01
for i in range(YTest.shape[0]):
    number = c_test[i]  # Klasse
    YTest[i, number] = 0.99
    
print('dataset: ', XTrain.shape, XTrain.dtype)
print('labelset:', YTest.shape)

model = keras.Sequential(
    [
        keras.Input(shape=(50, 50, 3)),
        layers.Conv2D(32, kernel_size=(3, 3), activation="relu"),
        layers.MaxPooling2D(pool_size=(2, 2)),
        layers.Conv2D(64, kernel_size=(3, 3), activation="relu"),
        layers.MaxPooling2D(pool_size=(2, 2)),
        layers.Flatten(),
        layers.Dropout(0.5),
        layers.Dense(43, activation="softmax"),
    ]
)
model.compile(loss='mean_squared_error', optimizer='adam', metrics=['accuracy'])
model.fit(XTrain, YTrain, batch_size=24, epochs=50, verbose=True, validation_split=0.1)

score = model.evaluate(XTest, YTest, verbose=False)
print('Test score:', score[0])
print('Test accuracy:', score[1])


print("fertisch")

Using TensorFlow backend.


1.13.1


FileNotFoundError: [Errno 2] No such file or directory: 'Verkehrszeichen.zip'

In [ ]:

#Loading Test Image 1
img = keras.preprocessing.image.load_img(
    "Stop_Schild.jpg", )
img = img.transpose(Image.ROTATE_270)
img = img.resize((50, 50), resample=Image.LANCZOS)
#Bild Anzeigen
fig = plt.figure(1, figsize=(9,5))
ax = fig.add_subplot(1, 2, 1)
ax.imshow(img)
ax.axis('off')
ax.set_title('Stop_Schild')
img_array = keras.preprocessing.image.img_to_array(img)
img_array = tf.expand_dims(img_array, 0)  # Create batch axis
print("Stop_Schild")
#print(img_array.shape, img_array.dtype)
#Bild identifizieren
predictions = model.predict(img_array)
score = np.argmax(predictions, axis = 1)
print(score)
print(" ")


#Loading Test Image 2
img = keras.preprocessing.image.load_img(
    "Vorfahrt_Schild.jpg", )
img = img.transpose(Image.ROTATE_270)
img = img.resize((50, 50), resample=Image.LANCZOS)
#Bild Anzeigen
ax = fig.add_subplot(1, 2, 2)
ax.imshow(img)
ax.axis('off')
ax.set_title('Vorfahrt_Schild')
img_array = keras.preprocessing.image.img_to_array(img)
img_array = tf.expand_dims(img_array, 0)  # Create batch axis
print("Vorfahrt_Schild")
#print(img_array.shape, img_array.dtype)
#Bild identifizieren
predictions = model.predict(img_array)
score = np.argmax(predictions, axis = 1)
print(score)


print("""
Klassenlabels:
Nr.12 = Vorfahrtsschild
Nr.14 = Stopschild
      """)

In [ ]:
predict = model.predict(XTest)
classes = np.argmax(predict, axis = 1)

erorrs = 0
error_data = []
error_num = []
correct_num = []

for x in range (XTest.shape[0]):
    
    classes1 = classes [x]
    data = XTest[x]
    num = c_test [x]
   
    
    if (classes1 != num):
        errors += 1
        error_data.append(data)
        error_num.append(classes1)
        correct_num.append(num)
        
nr = 6
nc = 10
fig = plt.figure(1, figsize=(12,8))

for i in range(1, nr*nc+1):
        ax = fig.add_subplot(nr,nc,i)
        ax.imshow(error_data[i-1], cmap='gray')
        # ax.imshow(images_original[i-1])
        ax.axis('off')
        ax.text(x=1, y=5, s = str(correct_num[i]), color= "orange")
        ax.text(x=1, y=46, s = "Result:", color= "orange")
        ax.text(x=25, y=46, s = str(error_num[i]), color= "orange")
        
plt.tight_layout()